<h2 style="text-align: center;">How to extract a light curve and spectrum for an EPIC point-like source</h2>
<br>
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px; text-align: left;">
			<p><b>Introduction</b></p>
			<p style="text-align: justify;">This thread contains a step-by-step recipe to extract a light curve and a spectrum of a point-like source which is valid for all the EPIC X-ray cameras. In the case of the light curve, it includes subtracting the background and correcting the light curve for exposure losses.</p>
            <p style="text-align: justify;">The purpose of this jupyter notebook thread is to illustrate how to use SAS within python notebooks. For an in-depth explanation on how to extract light curves and spectra for an EPIC point-like source using SAS, please refer to the standard SAS threads,</p>
                <ul>
                <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-timing">Extraction and correction of an x-ray light curve for a point-like source</a></li>
                <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-mos-spectrum">Spectral analysis of MOS poin-like sources</a></li>
                <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-pn-spectrum">How to extract pn spectra of a point-like source and associated matrices</a></li>
                </ul>
			<p><b>Expected Outcome</b></p>
			<p style="text-align: justify;">Spectrum and corrected light curve of a point-like source extracted from the XMM-Newton EPIC instruments.</p>
			<p><b>SAS Tasks to be Used</b></p>
			<ul>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/evselect/index.html" target="_parent"><tt>evselect</tt></a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epiclccorr/index.html" target="_parent"><tt>epiclccorr</tt></a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/arfgen/index.html" target="_parent"><tt>arfgen</tt></a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/rmfgen/index.html" target="_parent"><tt>rmfgen</tt></a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/backscale/index.html" target="_parent"><tt>backscale</tt></a></li>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/specgroup/index.html" target="_parent"><tt>specgroup</tt></a></li>
			</ul>
			<p><b>Prerequisites</b></p>
			<p style="text-align: justify;">It is assumed that the processed event lists, like the ones produced by the SAS tasks <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a>, and corresponding attitude and summary files as well as the <tt>ccf.cif</tt> file are available. Calibrated event lists may also be obtained as a starting point for this thread from the archive.</p>
			<ul>
				<li><a href="https://www.cosmos.esa.int/documents/332006/918155/sas-startup.ipynb" target="_parent">SAS Startup Thread in Python</a> (<a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-startup-in-python" target="_parent">html</a>)</li>
				<li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-epic-reprocessing" target="_parent">How to reprocess ODFs to generate calibrated and concatenated EPIC event lists Thread</a> (<a href="https://www.cosmos.esa.int/documents/332006/918155/epic-reprocessing.ipynb" target="_parent">html</a>)</li>
			</ul>
			<p><b>Useful Links</b></p>
			<ul>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/pysas/index.html"><tt>pysas</tt></a></li>
				<li><a href="https://www.cosmos.esa.int/documents/332006/918155/epic-bkgfiltering_singleevt.ipynb">How to filter EPIC event lists for flaring particle background in Python</a> (<a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-epic-filterbackground-in-python">html</a>)</li>
                <li><a href="https://het.as.utexas.edu/HET/Software/pyDS9/">pyds9 Documentation</a></li>
                <li><a href="https://heasarc.gsfc.nasa.gov/xanadu/xspec/python/html/index.html">pyxspec Documentation</a></li>
			</ul>
			<p><b><a href="#cav">Caveats</a></b></p>
			<h4>Last Reviewed: <i>25 May 2023, for <tt>SAS v21.0</tt></i></h4>
			<h4>Last Updated: <i>25 May 2023</i></h4>
			</td>
		</tr>
	</tbody>
</table>
</center>

<hr />
<h2>Procedure</h2>
<p>As an example case, we will consider the extraction of a spectrum and a light curve from a pn event list (<tt>PN_evt.fits</tt>). The same recipe applies for MOS. We highlight here the general steps which are included in the notebook cells below.<br />
&nbsp;</p>
<ul>
	<ol>
    <li>Set up your SAS environment (see <b>Prerequisites</b> for this thread at the top of the page).<br />
	&nbsp;</li>
	<li>Extract an image (in sky coordinates in this example; extraction in detector - <tt>DET[XY]</tt> - coordinates is possible as well).<br />
	<br />
	&nbsp; <tt>evselect table=PN_evt.fits imagebinning=binSize imageset=PNimage.img withimageset=yes \<br />
	&nbsp; &nbsp; xcolumn=X ycolumn=Y ximagebinsize=80 yimagebinsize=80</tt><br />
	&nbsp;</li>
	<li>Select the region in the image from which the spectrum and the light curve shall be accumulated. Lets assume its a circular region where the Centre coordinates are <tt>(27389.1,37183.40)</tt> and the radius <tt>800</tt>. Units of sky coordinates (X,Y) are <tt>0.05 arcsec</tt>, hence the radius in our example is <tt>40 arcsec</tt>.<br />
	&nbsp;</li>
     <li style="text-align: justify;">Repeat the previous step to determine the region from which the background for the spectrum and light curve is to be extracted. Lets assume its a circle, centered in <tt>(28855.1,40501.3)</tt> and radius also <tt>800</tt> pixels (have a look at the "<i>EPIC status of calibration and data analysis</i>" document <a href="https://xmmweb.esac.esa.int/docs/documents/CAL-TN-0018.pdf">(XMM-SOC-CAL-TN-0018)</a> for the latest recommendations on how to select source and background regions).<br />
	&nbsp;</li>        
	<li style="text-align: justify;">Now you can extract a source+background and background spectrum and light curve, using the selection regions and including a quality selection appropriate for the extraction of a spectrum and light curve.</li> 
    <h3>Light curve generation</h3> 
        &nbsp;      
        <ol>
        <li style="text-align: justify;">Extract a source light curve, for PN, taking good events, singles and doubles with an energy range between 200 and 10000 eV (<tt>#XMMEA_EP &amp;&amp; (PATTERN&lt;=4) &amp;&amp; (PI in [200:10000])</tt>); for MOS, taking good events, singles, doubles, triples and quadruples with an energy range between 200 and 10000 eV (<tt>#XMMEA_EM &amp;&amp; (PATTERN&lt;=12) &amp;&amp; (PI in [200:10000])</tt>). In the example below, the bin size is 100 seconds,<br />
	<br />
	&nbsp; <tt>evselect table=PN_evt.fits energycolumn=PI \<br />
	&nbsp; &nbsp; expression='#XMMEA_EP&amp;&amp;(PATTERN&lt;=4)&amp;&amp;((X,Y) IN circle(27389.1,37183.40,800))&amp;&amp;(PI in [200:10000])' \<br />
	&nbsp; &nbsp; withrateset=yes rateset="EPIC_PN_source_lightcurve.lc" timebinsize=100 \<br />
	&nbsp; &nbsp; maketimecolumn=yes makeratecolumn=yes </tt><br />
	<br />
	The parameter <tt>makeratecolumn=yes</tt> produces a light curve in count rates (with errors). Otherwise the light curve is produced in counts (without errors).<br />
	&nbsp;</li>
	<li>Extract a background light curve, using all the selection expressions defined so far, and the same bin size (100 seconds) and energy range as for the source region,<br />
	<br />
	&nbsp; <tt>evselect table=PN_evt.fits energycolumn=PI \<br />
	&nbsp;&nbsp; expression='#XMMEA_EP&amp;&amp;(PATTERN&lt;=4)&amp;&amp;((X,Y) IN circle(28855.1,40501.3,800))&amp;&amp;(PI in [200:10000])' \<br />
	&nbsp;&nbsp; withrateset=yes rateset="EPIC_PN_background_lightcurve.lc" timebinsize=100 \<br />
	&nbsp;&nbsp; maketimecolumn=yes makeratecolumn=yes </tt><br />
	<br />
	The light curves are OGIP-complaint, and therefore can be processed by standard XRONOS-like LHEASOFT packages.<br />
	&nbsp;</li>
	<li style="text-align: justify;">However, light curves obtained in such a way should be corrected for various effects affecting the detection efficiency, such as vignetting, bad pixels, PSF variations and quantum efficiency, as well as for variations affecting the stability of the detection within the exposure, like dead time and GTIs. Since all these effects can affect in a different manner source and background light curves, the background subtraction has to be done accordingly. A SAS task, <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epiclccorr/index.html"><tt>epiclccorr</tt></a>, performs all of these corrections at once. It requires as input both light curves (which are used to establish the binning of the final corrected background subtracted light curve) and the event file. This is done with a simple command line call:<br />
	<br />
	&nbsp; <tt>epiclccorr srctslist=EPIC_PN_source_lightcurve.lc eventlist=PN_evt.fits  \<br /> &nbsp;      
    &nbsp; outset=EPIC_PN_corrected_lightcurve.lc \<br />
	&nbsp; &nbsp; bkgtslist=EPIC_PN_background_lightcurve.lc withbkgset=yes applyabsolutecorrections=yes </tt><br />
	&nbsp;</li>
        </ol>
        <h3>Spectrum generation</h3> 
        &nbsp;
        <ol>
        <li style="text-align: justify;">Extract a source spectrum, for PN, taking good events, singles and doubles (<tt>#XMMEA_EP &amp;&amp; (PATTERN&lt;=4)</tt>); for MOS, taking good events, singles, doubles, triples and quadruples (<tt>#XMMEA_EM &amp;&amp; (PATTERN&lt;=12)</tt>). It is important to check <tt>withspecranges</tt> and use the following spectral bin range, <tt>specchannelmin=0</tt> and <tt>specchannelmax=20479</tt> (for MOS <tt>specchannelmin=0</tt> and <tt>specchannelmax=11999</tt>), to accumulate the spectrum.<br />
	     <br />
         &nbsp; <tt>evselect table=PN_evt.fits withspectrumset=yes \<br />
         &nbsp; &nbsp; spectrumset=EPIC_PN_source_spectrum.fits \<br />
         &nbsp; &nbsp; energycolumn=PI spectralbinsize=5 withspecranges=yes specchannelmin=0 specchannelmax=20479 \<br />
         &nbsp; &nbsp; expression='(FLAG==0)&amp;&amp;(PATTERN&lt;=4)&amp;&amp;((X,Y) IN circle(27389.1,37183.40,800))'</tt><br />
         <br />              
         </li>
         <li>Extract a background spectrum, using all the selection expressions defined so far,<br />
         <br />
         &nbsp; <tt>evselect table=PN_evt.fits withspectrumset=yes \<br />
         &nbsp; &nbsp; spectrumset=EPIC_PN_background_spectrum.fits \<br />
         &nbsp; &nbsp; energycolumn=PI spectralbinsize=5 withspecranges=yes specchannelmin=0 specchannelmax=20479 \<br />
         &nbsp; &nbsp; expression='(FLAG==0)&amp;&amp;(PATTERN&lt;=4)&amp;&amp;((X,Y) IN circle(28855.1,40501.3,800))'</tt><br />
         <br />              
         </li>   
         <li style="text-align: justify;">Calculate the area of source and background region used to make the spectral files. The area is written into the header of the SPECTRUM table of the file as keyword BACKSCAL.<br />
	     <br />
         &nbsp; <tt>backscale spectrumset=EPIC_PN_source_spectrum.fits badpixlocation=PN_evt.fits</tt><br />
         &nbsp; <tt>backscale spectrumset=EPIC_PN_background_spectrum.fits badpixlocation=PN_evt.fits</tt><br />
         <br />              
         </li> 
         <li style="text-align: justify;">Generate a redistribution matrix,<br />
         <br />
         &nbsp; <tt>rmfgen spectrumset=EPIC_PN_source_spectrum.fits rmfset=EPIC_PN.rmf</tt><br />
         <br />
         </li>              
         <li style="text-align: justify;">Generate an ancillary file,<br />
         <br />   
         &nbsp; <tt>arfgen spectrumset=EPIC_PN_source_spectrum.fits arfset=EPIC_PN.arf \<br />
         &nbsp; &nbsp; withrmfset=yes rmfset=EPIC_PN.rmf \<br />
         &nbsp; &nbsp; badpixlocation=PN_evt.fits detmaptype=psf</tt><br />             
         <br />
         </li>    
         <li style="text-align: justify;">Rebin the spectrum and link associated files. In the following example, the spectrum is rebinned in order to have at least 25 counts for each background-subtracted spectral channel and not to oversample the intrinsic energy resolution by a factor larger then 3. <br />
	     <br /> 
         &nbsp; <tt>specgroup spectrumset=EPIC_PN_source_spectrum.fits \<br />
         &nbsp; &nbsp; mincounts=25 oversample=3 \<br />
         &nbsp; &nbsp; rmfset=EPIC_PN.rmf arfset=EPIC_PN.arf backgndset=EPIC_PN_background_spectrum.fits \<br />
         &nbsp; &nbsp; groupedset=EPIC_PN_spectrum_grp.fits</tt><br /> 
         </li>
         <br />  
         <li style="text-align: justify;">Fit the grouped spectrum in <tt>xspec</tt>.</li>
        </ol>
    </ol> 
</ul>
<hr />

<p style="text-align: justify;"><b>In order to run the following blocks, SAS needs to be inizialized in the terminal from which the Jupyter nootebook has been opened. This has to be done prior to launching the notebook. Follow the steps provided in the <i>SAS Startup Thread in Python</i>.</b></p>

<p style="text-align: justify;">Import the following Python libraries,</p>

In [ ]:
from pysas.wrapper import Wrapper as w
import os
import os.path
from os import path
import matplotlib.pyplot as plt
import numpy as np
from astropy.io import fits
import pyds9
from xspec import *
import re

<p style="text-align: justify;">Before we start, lets see what we have already defined in terms of SAS variables,</p>

In [ ]:
inargs = []
t = w('sasver', inargs)
t.run()

<p style="text-align: justify;">We still need to define the <tt>SAS_ODF</tt> and <tt>SAS_CCF</tt> variables (make sure the SAS_CCFPATH is also defined). Use the SAS task <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/startsas/index.html"><tt>startsas</tt></a> as described in the <i>SAS Startup Thread in Python</i> to download an ODF. For this thread, we will assume that an ODF has already been downloaded. We will use the ODF with id <tt>010486050</tt> as an example and assume that there is already a directory (<tt>sas_file</tt> in the block below) with an existing <tt>CIF</tt> and SAS Summary File. In the block below introduce the absoute path to the <tt>Working directory</tt> (finished with '/') and the location of the <tt>CIF</tt> and SAS Summary File,</p>

<i><u>Note:</u> the path to the <tt>CIF</tt> and SAS Summary File must be an absolute path begining with '/'.</i>

In [ ]:
work_dir = 'absolute_path_to_wrk_directory'
sas_file = 'absolute_path_to_cifSUMSAS_directory'

In [ ]:
inargs = [f'sas_ccf={sas_file}ccf.cif', f'sas_odf={sas_file}0466_0104860501_SCX00000SUM.SAS', f'workdir={work_dir}']

In [ ]:
w('startsas', inargs).run()

<p style="text-align: justify;">This process should have defined the <tt>SAS_CCF</tt> an <tt>SAS_ODF</tt> variables.</p> 

<p style="text-align: justify;">In the following blocks we will filter an EPIC-pn event file for periods of high background <i>flaring</i> activity as an example. The same procedure is valid as well for an EPIC-MOS event file.</p>

<ul>
    <li style="text-align: justify;">Introduce the EPIC-pn event file to process including the absolute path. If no event files are available, please follow <a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-epic-reprocessingplease"><i>How to reprocess ODFs to generate calibrated and concatenated EPIC event lists</i></a> thread first.</li>
</ul>

In [ ]:
eventfile = work_dir+'0466_0104860501_EPN_S003_ImagingEvts.ds'

In [ ]:
print("Checking for EPIC-pn Event Files ..... \n")
# Check if epproc has already run.
if os.path.isfile(eventfile):
    print ("File "+eventfile+" exists. \n")
else:
    print ("File "+eventfile+" does not exist, please check. \n")

<ul>
    <li style="text-align: justify;">Produce an image from this event file. The image is produced in sky coordinates (X,Y), but it can also be produced in detector coordinates (DETX,DETY).</li>
</ul>

In [ ]:
# Define some parameters to produce the image and the name of the output file

xbin=80     # xbin size
ybin=80     # ybin size
xcoord='X'  # coordinate system
ycoord='Y'  # coordinate system

out_IMFile   = work_dir+'EPIC_PN_Image.fit'  # Name of the output Image file 

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'table={eventfile}','imagebinning=binSize',f'imageset={out_IMFile}','withimageset=yes',f'xcolumn={xcoord}',f'ycolumn={ycoord}',f'ximagebinsize={xbin}',f'yimagebinsize={ybin}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce an image

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">The following block will open a ds9 window with the selected image, set the color map to <i>bb</i> and the scale to <i>log</i>. </li>
    <li style="text-align: justify;">This image can be used to select a <i>source</i> and <i>background</i> regions from which to extract a light curve for the source with its corresponding background.</li> 
</ul>

In [ ]:
# Visualize the image with ds9

d = pyds9.DS9()
d.set("file "+out_IMFile)
d.set('cmap bb')
d.set('scale log')

<ul>
    <li style="text-align: justify;">Go to the ds9 window and select a <i>source</i> region using the tools provided within ds9. In this example, a circular region must be chosen (this can be controlled or changed in the following block). Do the same for the <i>background</i> region, using either circular or annulus shapes. The color of the <i>source</i> region must be changed to <b>white</b> in ds9. For the background region, use any other color except white, for example red, but the color must be also changed explicitly to include the #color identifier in the region information. The blocks below also accept an annulus for the background region. We will use this information to distinguish the source and background regions while parsing the information to Python. After this, execute the block below.</li>
        
<li style="text-align: justify;"> The following block should output the coordinates that have been extracted for the <i>source</i> and <i>background</i> region from the ds9 window and that will be used in the following blocks to extract the light curve and spectrum from the chosen source. Before proceeding with the notebook, double check that both regions have a #color identifier, and that the one from the <i>source</i> region is set to <b>white</b>.</li>
</ul>

In [ ]:
# Check the information that ds9 has about the regions defined in the ds9 window.

print(d.get("regions"))

In [ ]:
# Extract the relevant information from the ds9 regions.

region1=(re.split("circle|annulus",d.get("regions").partition("physical")[2]))[1].replace('(','').replace(')','').replace('#',',')
region2=(re.split("circle|annulus",d.get("regions").partition("physical")[2]))[2].replace('(','').replace(')','').replace('#',',')

print("Identified source region: ", region1)
print("Identified source region: ", region2)

In [ ]:
# Identify source and background regions using the 'white' color.

c1=region1.partition("color")[2].replace('=','').replace('\n','')
if(c1=='white'):
    regionsrc = region1
    regionbkg = region2
else:
    regionsrc = region2
    regionbkg = region1

# Save and print selected region coordinates.

x_source = regionsrc.split(",")[0].replace('\n','')
y_source = regionsrc.split(",")[1].replace('\n','')
r_source = regionsrc.split(",")[2].replace('\n','')
print("The coordinates of the selected source region are: \n")
print("  x_source = ", x_source, "(physical)")
print("  y_source = ", y_source, "(physical)")
print("  r_source = ", r_source, "(physical) \n")   
    
x_bkg = regionbkg.split(",")[0].replace('\n','')
y_bkg = regionbkg.split(",")[1].replace('\n','')
r_bkg = regionbkg.split(",")[2].replace('\n','')
print("The coordinates of the selected background region are: \n")
print("  x_bkg = ", x_bkg, "(physical)")
print("  y_bkg = ", y_bkg, "(physical)")
print("  r_bkg = ", r_bkg, "(physical) \n")   

# If the background is an annulus, save and print R2.

if "annulus" in str(d.get("regions")):
    r2_bkg = regionbkg.split(",")[3].replace('\n','')
    print("  r2_bkg = ", r2_bkg, "(physical)")   

<ul>
    <li style="text-align: justify;">With both <i>source</i> and <i>background</i> regions defined, you can now start to extract the corresponding light curves and spectra.</li>
</ul>

<h2>Lightcurve Extraction</h2>

<ul>
    <li style="text-align: justify;">First, produce a light curve for the <i>source</i> region. In this example, we will produce a light curve for pn with a bin size of 100 seconds.</li>
   <li style="text-align: justify;">Use the <i>source</i> region and include a quality selection appropriate for a light curve extraction:<br>
   <ul>
   <li style="text-align: justify;"> For PN, take good events, singles and doubles with an energy range between 200 and 10000 eV (#XMMEA_EP && (PATTERN<=4) && (PI in [200:10000]));</li>
   <li style="text-align: justify;"> For MOS, take good events, singles, doubles, triples and quadruples with an energy range between 200 and 10000 eV (#XMMEA_EM && (PATTERN<=12) && (PI in [200:10000])).</li>
   </ul>
   <br>
   <i>NOTE: The parameter <i>makeratecolumn=yes</i> in the call to the SAS task <i>evselect</i> below produces a light curve in count rates (with errors). Otherwise, the light curve is produced in counts (without errors).</i>
</ul>

In [ ]:
# Function to plot Lightcurve
def plotLC(plt,threshold,fileName):        
        if fileName != "NOT FOUND":
            fitsFile = fits.open(fileName)   
            prihdu   = fitsFile[1].header
            if ('CUTVAL' in prihdu):
                threshold = prihdu['CUTVAL']

            cols    = fitsFile[1].columns
            colName = None
            for i,x  in enumerate(cols.names):
                if "RATE" in x:
                    colName = cols.names[i]
                if "COUNTS" in x:
                    colName = cols.names[i]        

            data = fitsFile[1].data   
            
            xdata = data.field('TIME') - min(data.field('TIME')) # extract the x data column
            ydata = data.field(colName)

            xmax=np.amax(xdata) 
            xmin=np.amin(xdata) 

            plt.plot(xdata,ydata,label=fileName) # plot the data

            if colName == 'RATE':
                plt.title("Lightcurve")
                plt.xlabel("Time (s)")
                plt.ylabel("Cts/s")
            else:
                plt.title("Lightcurve")
                plt.xlabel("Time (s)")
                plt.ylabel("Counts")

            if (threshold != 'None'):
                if (colName == 'COUNTS'):
                    threshold=float(threshold)*100.

                y2data = [threshold]*len(xdata)            
                plt.plot(xdata,y2data)
                plt.text(xmin+0.1*(xmax-xmin), threshold+0.01*threshold, str(threshold)+" cts/sec", ha='center')        
 
            fitsFile.close()   
            
        else:
            print("File not found "+fileName+"\n")

In [ ]:
# Extract the source region lightcurve

# Define some parameters for filtering the event file and define the lightcurve binning

q_flag       = "#XMMEA_EP" # Quality flag for EPIC pn
n_pattern    = 4           # Pattern selection
pn_pi_min    = 200.        # Low energy range eV
pn_pi_max    = 10000.      # High energy range eV
lc_bin       = 100         # Lightcurve bin in secs

# Define the output ligthcurve file name

in_LCSRCFile = work_dir+'EPIC_PN_source_lightcurve.lc'   # Name of the output source lightcurve

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'{q_flag}&&(PATTERN<={n_pattern})&&((X,Y) IN circle({x_source},{y_source},{r_source}))&&(PI in [{pn_pi_min}:{pn_pi_max}])'  # event filter expression
inargs     = [f'table={eventfile}','energycolumn=PI','withrateset=yes',f'rateset={in_LCSRCFile}',
              f'timebinsize={lc_bin}','maketimecolumn=yes','makeratecolumn=yes',f'expression={expression}']

print("   Filter expression to use: "+expression+" \n")
print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the source region light curve

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Run the following cell to inspect the created <i>source</i> light curve.</li>
</ul>

In [ ]:
# Inspect light curve

pn_threshold = 1.0          # cts/sec (only used here for display purposes. Draws a horizontal line at this value)
plt.figure(figsize=(20,8))  # Size of figure

plotLC(plt,pn_threshold,in_LCSRCFile) # Plot source region light curve

plt.legend()

<ul>
    <li style="text-align: justify;">Second, produce a lightcurve for the <i>background</i> region, in the same energy range and using the same filtering criteria.</li>
</ul>

In [ ]:
# Extract the background region light curve

# Define some parameters for filtering the event file and define the lightcurve binning

q_flag       = "#XMMEA_EP" # Quality flag for EPIC pn
n_pattern    = 4           # Pattern selection
pn_pi_min    = 200.        # Low energy range eV
pn_pi_max    = 10000.      # High energy range eV
lc_bin       = 100         # Lightcurve bin in secs

# Define the output ligthcurve file name

in_LCBKGFile = work_dir+'EPIC_PN_background_lightcurve.lc'   # Name of the output background lightcurve

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'{q_flag}&&(PATTERN<={n_pattern})&&((X,Y) IN circle({x_bkg},{y_bkg},{r_bkg}))&&(PI in [{pn_pi_min}:{pn_pi_max}])'  # event filter expression
inargs     = [f'table={eventfile}','energycolumn=PI','withrateset=yes',f'rateset={in_LCBKGFile}',
              f'timebinsize={lc_bin}','maketimecolumn=yes','makeratecolumn=yes',f'expression={expression}']

print("   Filter expression to use: "+expression+" \n")
print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the background region light curve

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Run the following cell to inspect the created <i>background</i> light curve.</li>
</ul>

In [ ]:
# Inspect light curve

pn_threshold = 0.01         # cts/sec (only used here for display purposes. Draws a horizontal line at this value)
plt.figure(figsize=(20,8))  # Size of figure

plotLC(plt,pn_threshold,in_LCBKGFile) # Plot background region light curve

plt.legend()

<ul>
    <li style="text-align: justify;"> The produced light curves can be corrected for a number of effects affecting the detection efficiency, such as vignetting, bad pixels, PSF variations and quantum efficiency, as well as for variations affecting the stability of the detection within the exposure, like dead time and GTIs. Since all these effects can affect in a different manner <i>source</i> and <i>background</i> light curves, the background subtraction has to be done accordingly.</li>
    <li style="text-align: justify;"> A SAS task, <i>epiclccorr</i>, performs all of these corrections at once. It requires as input both light curves (which are used to establish the binning of the final corrected background subtracted light curve) and the event file. This is done with a simple command line call:</li>
</ul>

In [ ]:
# Define the output corrected ligthcurve file name

in_LCFile = work_dir+'EPIC_PN_corrected_lightcurve.lc'   # Name of the output corrected lightcurve

In [ ]:
# Correct the light curve with the SAS task epiclccorr

# SAS Command
cmd        = "epiclccorr" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'eventlist={eventfile}',f'srctslist={in_LCSRCFile}',f'outset={in_LCFile}',
              f'bkgtslist={in_LCBKGFile}','withbkgset=yes','applyabsolutecorrections=yes']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the corrected light curve

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Run the following cell to inspect the created corrected light curve.</li>
    <br>
    <i>NOTE: make sure the previous block has finished running before proceeding with the next blocks. The task <i>epiclccorr</i> can take some time to run.</i>
</ul>

In [ ]:
# Inspect light curve

pn_threshold = 1.0          # cts/sec (only used here for display purposes. Draws a horizontal line at this value)
plt.figure(figsize=(20,8))  # Size of figure

plotLC(plt,pn_threshold,in_LCFile)          # Plot corrected light curve
plotLC(plt,pn_threshold,in_LCSRCFile)       # Plot source region light curve
plotLC(plt,pn_threshold,in_LCBKGFile)       # Plot background region light curve

plt.legend()

<h2>Spectra Extraction</h2>

<ul>
    <li style="text-align: justify;">First, produce a spectrum for the <i>source</i> region.</li>
   <li style="text-align: justify;">Use the <i>source</i> region and include a quality selection appropriate for spectrum extraction:<br>
   <ul>
   <li style="text-align: justify;"> For PN, take good events, singles and doubles (#XMMEA_EP&&(PATTERN<=4));</li>
   <li style="text-align: justify;"> For MOS, take good events, singles, doubles, triples and quadruples (#XMMEA_EM&amp;&amp;(PATTERN&lt;=12)).</li>
   </ul>
</ul>

In [ ]:
# Extract the source region spectrum

# Define some parameters for filtering the event file

q_flag       = "#XMMEA_EP" # Quality flag for EPIC pn
n_pattern    = 4           # Pattern selection

# Define the output ligthcurve file name

in_SPSRCFile = work_dir+'EPIC_PN_source_spectrum.fits'   # Name of the output source spectrum

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'{q_flag}&&(PATTERN<={n_pattern})&&((X,Y) IN circle({x_source},{y_source},{r_source}))'  # event filter expression
inargs     = [f'table={eventfile}','withspectrumset=yes',f'spectrumset={in_SPSRCFile}',          
              'energycolumn=PI','spectralbinsize=5','withspecranges=yes','specchannelmin=0',
              'specchannelmax=20479',f'expression={expression}']
print("   Filter expression to use: "+expression+" \n")
print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the source spectrum

w(cmd, inargs).run()

<ul>
   <li style="text-align: justify;">Second, produce a spectrum for the background region, using the same filtering criteria.</li>
</ul>

In [ ]:
# Extract the source region spectrum

# Define some parameters for filtering the event file

q_flag       = "#XMMEA_EP" # Quality flag for EPIC pn
n_pattern    = 4           # Pattern selection

# Define the output ligthcurve file name

in_SPBKGFile = work_dir+'EPIC_PN_background_spectrum.fits'   # Name of the output background spectrum

In [ ]:
# SAS Command
cmd        = "evselect" # SAS task to be executed                  

# Arguments of SAS Command
expression = f'{q_flag}&&(PATTERN<={n_pattern})&&((X,Y) IN circle({x_bkg},{y_bkg},{r_bkg}))'  # event filter expression
inargs     = [f'table={eventfile}','withspectrumset=yes',f'spectrumset={in_SPBKGFile}',          
              'energycolumn=PI','spectralbinsize=5','withspecranges=yes','specchannelmin=0',
              'specchannelmax=20479',f'expression={expression}']
print("   Filter expression to use: "+expression+" \n")
print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task with the parameters to produce the background spectrum

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Third, run <tt>backscale</tt> on both spectra.</li>
</ul>

In [ ]:
# SAS Command
cmd        = "backscale" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'spectrumset={in_SPSRCFile}',f'badpixlocation={eventfile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task for the source spectrum

w(cmd, inargs).run()

In [ ]:
# SAS Command
cmd        = "backscale" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'spectrumset={in_SPBKGFile}',f'badpixlocation={eventfile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task for the background spectrum

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Fourth, generate a redistribution matrix. This task could take some time to run. Check the terminal or log to see when it finishes before executing the next cells.</li>
</ul>

In [ ]:
# Define some parameters for rmfgen

# Define the output redistribution matrix file name

in_RESPFile = work_dir+'EPIC_PN.rmf'   # Name of the output redistribution

In [ ]:
# SAS Command
cmd        = "rmfgen" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'spectrumset={in_SPSRCFile}',f'rmfset={in_RESPFile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task for generation of redistribution matrix

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Fifth, generate an ancillary file. This task could take some time to run. Check the terminal or log to see when it finishes before executing the next cells.</li>
</ul>

In [ ]:
# Define some parameters for rmfgen

# Define the output ancillary file name

in_ARFFile = work_dir+'EPIC_PN.arf'   # Name of the output ancillary

In [ ]:
# SAS Command
cmd        = "arfgen" # SAS task to be executed                  

print("   Checking for Response File ..... \n")
# Check if RESP file is available.
if os.path.isfile(in_RESPFile):
    print ("File "+in_RESPFile+" exists. \n")
else:
    print ("File "+in_RESPFile+" does not exist, please check. \n")
    
# Arguments of SAS Command
inargs     = [f'spectrumset={in_SPSRCFile}',f'arfset={in_ARFFile}',
              'withrmfset=yes',f'rmfset={in_RESPFile}',f'badpixlocation={eventfile}','detmaptype=psf']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task for generation of the ancillary file 

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Sixth, rebin the spectra and link associated files.</li>
</ul>

In [ ]:
# Define some parameters for specgruop

# Define the output ancillary file name

in_GRPFile = work_dir+'EPIC_PN_spectrum_grp.fits'   # Name of the output specgruop

In [ ]:
# SAS Command
cmd        = "specgroup" # SAS task to be executed                  

# Arguments of SAS Command
inargs     = [f'spectrumset={in_SPSRCFile}','mincounts=25','oversample=3',
              f'rmfset={in_RESPFile}',f'arfset={in_ARFFile}',
              f'backgndset={in_SPBKGFile}',f'groupedset={in_GRPFile}']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
# Execute the SAS task for generation of the ancillary file 

w(cmd, inargs).run()

<ul>
    <li style="text-align: justify;">Last, load the group spectral file in <tt>xspec</tt> and fit it with a given model.</li>
    <li style="text-align: justify;">In the following cells we show some basic commands that can be used as a guideline to plot, fit and interact with <tt>xspec</tt>. <tt>xspec</tt> will output the log to the terminal from which the notebook has been launched. The following blocks are all illustrative.</li>
</ul>

In [ ]:
# Before you start, clear all data and models

AllModels.clear()  # Clear all models
AllData.clear()    # Clear all data

In [ ]:
# Load the group spectral file

# The group file already contains in the header the names of all the necessary files needed by xspec
# (source and background spectra, response and ancillery files)

data1 = Spectrum(in_GRPFile)  # load spectra groupped file
AllData.show()                # inspect loaded data

In [ ]:
# Plot results by opening a window directly on the notebook

Plot.device = "/svg"

In [ ]:
# First inspection of the spectrum

Plot.xAxis = "keV"        # set X axis to energy units
Plot.xLog  = True         # log scale
Plot.yLog  = True         # log scale
Plot("data background")   # plot source and background spectra

<ul>
    <li style="text-align: justify;">In the plot above, you can see the <i>source</i> region spectrum (top panel) and the <i>background</i> region spectra (bottom panel).</li>
</ul>

In [ ]:
# Define a model and its parameters

model1 = Model("phabs*pow")   # powerlaw with absorption

In [ ]:
Xset.chatter 
# Fit model

data1.ignore("**-0.2 10.-**") # For the fit, ignore the range ourside (0.2-10.)
data1.ignore("bad")           # For the fit, ignore bad channels

Fit.nIterations = 100         # maximum number of iterations during fitting
Fit.statMethod  = "cstat"     # fit statistics to be used
Fit.perform()                 # perform fit
cl              = 2.706       # confidence level (90%)
Fit.error(str(cl)+" 1 2 3")   # derive errors at given confidence range for all parameters

fene_ini = 0.2                # Initial energy to derive flux (keV)
fene_end = 10.                # End energy to derive flux (keV)
AllModels.calcFlux(str(fene_ini)+" "+str(fene_end)+" err")  # derive the flux and error in the 0.2-10 keV energy range according to fitted model


In [ ]:
# Extract information from fitted model

nh       = model1(1).values[1]         # Model parameter 1
nherr    = AllModels(1)(1).error       # Error model parameter 1
alpha    = model1(2).values[0]         # Model parameter 2
alphaerr = AllModels(1)(2).error       # Error model parameter 2
norm     = model1(3).values[0]         # Model parameter 3
normerr  = AllModels(1)(3).error       # Error model parameter 3

dof      = Fit.dof                     # get fit dof
statv    = Fit.statMethod              # fit statistics method
stat     = Fit.statistic               # get value of fit statistics
tstatv   = Fit.statTest                # test statistics method
tstat    = Fit.testStatistic           # get value of test statistics
flux     = data1.flux                  # get flux

print(" Fit Statistics: \n")
print("   Value of fit stat: "+str(stat)+" ("+statv+")\n")
print("   Value of test stat: "+str(tstat)+" ("+tstatv+"\n")
print("   Fit dof: "+str(dof)+"\n")
print(" Model Parameters and their error: \n")
print("   Nh Value (10^22) : "+str(100.*nh)+" , "+str(nherr)+"\n")
print("   Alpha Value: "+str(alpha)+" , "+str(alphaerr)+"\n")
print("   Norm Value: "+str(norm)+" , "+str(normerr)+"\n")
print("   Flux Value ("+ str(fene_ini)+"-"+str(fene_end)+" keV) (ergs/cm^2/s): "+str(flux[0])+" , "+"("+str(flux[1])+", "+str(flux[2])+")\n")

In [ ]:
# Plot results by opening a window directly on the notebook

Plot.device = "/svg"

In [ ]:
# Plot data and folded model with residuals

Plot.xAxis = "keV"        # set X axis to energy units
Plot.xLog  = True         # log scale
Plot.yLog  = True         # log scale
Plot("ldata","residuals") # plot data and folded model, with residuals

<ul>
    <li style="text-align: justify;">In the plot above, you can see the <i>source</i> spectrum (top panel) and the residuals against the best fit model (bottom panel).</li>
</ul>

<hr />&nbsp;
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px;">
			<p><a name="cav"></a> <b>Caveats</b><br />
			<br />
			None</p>
			</td>
		</tr>
	</tbody>
</table>
</center>
&nbsp;

<hr />
<p>&nbsp;</p>